### Imports

In [1]:
from importlib import reload
import fds_tools
reload(fds_tools)
import common_tools
reload(common_tools)
import db_tools
reload(db_tools)
import duckdb
reload(duckdb)
import pandas as pd
from db_tools.mySQL_tools import Connection, ConnectionConfigType, MySQLConfig
from fds_tools.fake_users_generator import FakeUsersGenerator, Constants
from common_tools import CommonTools, PandasTools, DuckDBTools
import duckdb

In [8]:
import numpy as np
profiles_table = PandasTools.load_path('data/users/profiles.csv')
print(np.mean(profiles_table['age']), Constants.age_mean)
print(np.std(profiles_table['age']), Constants.age_std)

print(profiles_table[profiles_table['sex'] == 'male'].count() / profiles_table.count(), Constants.male_prob)


23.157601989133436 23.64
5.9747579659906265 6.04
user_id      0.721979
country      0.721979
city         0.721977
age          0.721979
sex          0.721979
latitude     0.721979
longitude    0.721979
dtype: float64 0.722


In [8]:
print(profiles_table.columns)
print(profiles_table[profiles_table['user_id'] == 11072])

Index(['user_id', 'country', 'city', 'age', 'sex', 'latitude', 'longitude'], dtype='object')
   user_id country          city  age   sex  latitude  longitude
0    11072  poland  starachowice   28  male   51.0374   21.07126


### Constants. Tables

In [6]:
users_cleaned = {}
users_vectors = {}

for chunk in pd.read_csv(f"{data_folder}/rating_complete.csv", chunksize=100000):
    chunk_cleaned = chunk[chunk['rating'] != -1]
    for index, row in chunk_cleaned.iterrows():
        user_id = row['user_id']
        anime_id = row['anime_id']
        rating = row['rating']
        users[user_id][anime_id] = rating

anime_data_pd['rating_complete_cleaned']

NameError: name 'data_folder' is not defined

In [5]:
players = anime_data_db["rating_complete"].filter("rating > 9")
# players = duckdb.query(f"""select * from {anime_data['rating_complete']}  where rating > 9""")
# players

al = anime_data_db["animelist"]
a  = anime_data_db["anime"]
f = duckdb.query("""
SELECT
    COUNT(DISTINCT al.user_id) AS n_users
FROM animelist AS al
JOIN anime AS a
    ON al.anime_id = a.MAL_ID
WHERE
    al.watching_status = 2
    AND al.rating != 0
    AND TRY_CAST(al.watched_episodes AS INTEGER) IS NOT NULL
    AND TRY_CAST(al.watched_episodes AS INTEGER) < TRY_CAST(a.Episodes AS INTEGER);
""").fetchone()[0]

f1 = duckdb.query("""
SELECT
    COUNT( * ) AS n_rows
FROM animelist AS al
WHERE al.rating == 0
""").fetchone()[0]

NameError: name 'anime_data_db' is not defined

In [ ]:
print(f, f1)
print(f/109224747*100)
print(f1/109224747)

104315 46827035
0.0955049133691287
0.4287218445102006


In [ ]:
import pandas as pd
from ydata_profiling import ProfileReport

df = pd.read_csv('data/anime.csv')
profile = ProfileReport(df, title="Profiling Report")

In [ ]:
# profile.to_widgets()
profile.to_notebook_iframe()

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [2]:
# получаем уникальные user_id без загрузки всего файла
t = CommonTools.find_not_honest_users()
print(t.head())
print(len(t))

InvalidInputException: Invalid Input Error: Error when sniffing file "data/anime_ranks/anime.csv".
It was not possible to automatically detect the CSV parsing dialect
The search space used was:
Delimiter Candidates: ',', '|', ';', '	'
Quote/Escape Candidates: ['(no quote)','(no escape)'],['"','(no escape)'],['"','"'],['"','''],['"','\'],[''','(no escape)'],[''','''],[''','"'],[''','\']
Comment Candidates: '\0', '#'
Encoding: utf-8
Possible fixes:
* Disable the parser's strict mode (strict_mode=false) to allow reading rows that do not comply with the CSV standard.
* Columns are set as: "columns = { 'MAL_id' : 'BIGINT', 'Episodes' : 'INTEGER'}", and they contain: 2 columns. It does not match the number of columns found by the sniffer: 35. Verify the columns parameter is correctly set.
* Make sure you are using the correct file encoding. If not, set it (e.g., encoding = 'utf-16').
* Set delimiter (e.g., delim=',')
* Set quote (e.g., quote='"')
* Set escape (e.g., escape='"')
* Set comment

In [ ]:
import os
import csv

users_csv = "data/users/profiles.csv"
con_type = ConnectionConfigType.real_connection_config
# print(con_type.host, con_type.port, con_type.user, con_type.password, con_type.database)
con = Connection.create(con_type)
cursor  = con.cursor()
print("Connected" if con.is_connected() else "Not connected")
# cursor.execute("""ALTER TABLE users
#     ADD COLUMN country VARCHAR(64) NULL,
#     ADD COLUMN city VARCHAR(64) NULL,
#     ADD COLUMN latitude FLOAT NULL,
#     ADD COLUMN longitude FLOAT NULL;""")
# con.close()
# con = Connection(con_type)

def to_int_safe(v):
    try:
        if v is None:
            return None
        s = str(v).strip()
        if s == "":
            return None
        return int(s)
    except:
        return None

def to_float_safe(v):
    try:
        s = str(v).strip()
        return float(s) if s else None
    except:
        return None

def insert_users_from_users_csv(cursor, batch_users: int = 10000):
    if not os.path.exists(users_csv):
        return 0
    buf, total = [], 0
    with open(users_csv, encoding="utf-8") as f:
        for r in csv.DictReader(f):
            # print(r)
            uid = to_int_safe(r.get("user_id") or r.get("userID"))
            if uid is None:
                continue
            buf.append((
                uid,
                r.get("sex"),
                to_int_safe(r.get("age")),
                'NULL',
                r.get("country"),
                r.get("city"),
                to_float_safe(r.get("latitude")),
                to_float_safe(r.get("longitude")),
            ))
            if len(buf) >= batch_users:
                cursor.executemany("""
                                   INSERT INTO users (userID, sex, age, geoLocation, country, city, latitude, longitude)
                                   VALUES (%s, %s, %s, %s, %s, %s, %s, %s)
                                   ON DUPLICATE KEY UPDATE
                                   sex = VALUES(sex),
                                   age = VALUES(age),
                                   geoLocation = NULL,
                                   country = VALUES(country),
                                   city = VALUES(city),
                                   latitude = VALUES(latitude),
                                   longitude = VALUES(longitude)
                                   """,
                                   buf)
                total += len(buf)
                buf.clear()
            if total % 1000 == 0:
                print(total)
    if buf:
        cursor.executemany("""
                           INSERT INTO users (userID, sex, age, geoLocation, country, city, latitude, longitude)
                           VALUES (%s, %s, %s, %s, %s, %s, %s, %s)
                           ON DUPLICATE KEY UPDATE
                           sex = VALUES(sex),
                           age = VALUES(age),
                           geoLocation = NULL,
                           country = VALUES(country),
                           city = VALUES(city),
                           latitude = VALUES(latitude),
                           longitude = VALUES(longitude)
                           """,
                           buf)
        total += len(buf)
    con.commit()
    return total

insert_users_from_users_csv(con.cursor())
con.commit()
con.close()

Connected
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0


In [ ]:
cursor.execute("""show processlist""")